<a href="https://colab.research.google.com/github/entc-17-fyp-20/CM_Normal_Behaviour_Modeling/blob/main/CNN1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Import libraries and datasets

In [1]:
# multivariate data preparation
from numpy import array
from numpy import hstack
import pandas as pd
import numpy as np
from sklearn import preprocessing

from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers.convolutional import Conv1D
from keras.layers.convolutional import MaxPooling1D

import plotly.graph_objects as go

In [2]:
# split a multivariate sequence into samples
def split_sequences(sequences, n_steps):
	X, y = list(), list()
	for i in range(len(sequences)):
		# find the end of this pattern
		end_ix = i + n_steps
		# check if we are beyond the dataset
		if end_ix > len(sequences):
			break
		# gather input and output parts of the pattern
		seq_x, seq_y = sequences[i:end_ix, :-1], sequences[end_ix-1, -1]
		X.append(seq_x)
		y.append(seq_y)
	return array(X), array(y)

In [3]:
#@title Select Dataset New { display-mode: "form" }
turbine = 'T01' #@param ["T01", "T02","T03","T22","T34","T54"]
path = '/content/drive/MyDrive/IIoT - Wind Turbine/FYP/Dataset/Merged/' + turbine + '.csv'
df = pd.read_csv(path)
df['Date_Time'] = pd.to_datetime(df['Date_Time'], format="%Y-%m-%d %H:%M:%S")

In [4]:
#@title Window size { display-mode: "form" }
n_steps = 5 #@param {type:"slider", min:2, max:6, step:1}

In [5]:
#@title Select scaling method { display-mode: "form" }
method = 'MinMax' #@param ["Normalize", "MinMax"]

df_time = df["Date_Time"]
df.drop("Date_Time", axis='columns', inplace=True)
column_names = df.columns

if method == "Normalize":
  d = preprocessing.normalize(df, axis=0)
else:
  scaler = preprocessing.MinMaxScaler()
  d = scaler.fit_transform(df)

df = pd.DataFrame(d, columns=column_names)
df["Date_Time"] = df_time
df = df.set_index(df['Date_Time'])

In [6]:
df1 = df[:'2017-03-19 05:10:00']
df2 = df['2017-04-13 16:10:00':"2017-05-31 00:00:00"]
df3 = df["2017-06-01 00:00:00":"2017-07-20 02:50:00"]
df4 = df['2017-07-21 08:10:00':'2017-08-14 05:20:00']
df5 = df['2018-01-15 12:00:00':"2018-02-10 23:50:00"]
df6 = df['2018-02-13 00:00:00':'2018-04-21 06:40:00']
df7 = df['2018-05-01 10:10:00':"2018-05-31 00:00:00"]
df8 = df['2018-06-01 00:00:00':'2018-08-14 06:50:00']
df9 = df['2018-08-21 07:00:00':]

n_features = len(df1.columns.tolist())-3

In [7]:
df1

Ambient_Temperature  ...           Date_Time
Date_Time                                 ...                    
2017-01-01 00:00:00             0.225806  ... 2017-01-01 00:00:00
2017-01-01 00:10:00             0.225806  ... 2017-01-01 00:10:00
2017-01-01 00:20:00             0.225806  ... 2017-01-01 00:20:00
2017-01-01 00:30:00             0.209677  ... 2017-01-01 00:30:00
2017-01-01 00:40:00             0.209677  ... 2017-01-01 00:40:00
...                                  ...  ...                 ...
2017-03-19 04:30:00             0.387097  ... 2017-03-19 04:30:00
2017-03-19 04:40:00             0.370968  ... 2017-03-19 04:40:00
2017-03-19 04:50:00             0.387097  ... 2017-03-19 04:50:00
2017-03-19 05:00:00             0.387097  ... 2017-03-19 05:00:00
2017-03-19 05:10:00             0.387097  ... 2017-03-19 05:10:00

[11120 rows x 15 columns]

# Model

In [8]:
def create_model():
# define model
  model = Sequential()
  model.add(Conv1D(filters=64, kernel_size=2, activation='relu', input_shape=(n_steps, n_features)))
  model.add(MaxPooling1D(pool_size=2))
  model.add(Flatten())
  model.add(Dense(50, activation='relu'))
  model.add(Dense(1))
  model.compile(optimizer='adam', loss='mse')
  return model

# Training 

In [33]:
df1.drop("Date_Time", axis='columns', inplace=True)
df1.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df1.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df1 = df1[cols]
df1 = df1.to_numpy()

# convert into input/output
X1, y1 = split_sequences(df1, n_steps)
print(X1.shape, y1.shape)

(11116, 5, 12) (11116,)


/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [34]:
df2.drop("Date_Time", axis='columns', inplace=True)
df2.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df2.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df2 = df2[cols]
df2 = df2.to_numpy()

# convert into input/output
X2, y2 = split_sequences(df2, n_steps)
print(X2.shape, y2.shape)

(6812, 5, 12) (6812,)


/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [35]:
df3.drop("Date_Time", axis='columns', inplace=True)
df3.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df3.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df3 = df3[cols]
df3 = df3.to_numpy()

# convert into input/output
X3, y3 = split_sequences(df3, n_steps)
print(X3.shape, y3.shape)

(7047, 5, 12) (7047,)


/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [36]:
df4.drop("Date_Time", axis='columns', inplace=True)
df4.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df4.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df4 = df4[cols]
df4 = df4.to_numpy()

# convert into input/output
X4, y4 = split_sequences(df4, n_steps)
print(X4.shape, y4.shape)

(3425, 5, 12) (3425,)


/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [37]:
df5.drop("Date_Time", axis='columns', inplace=True)
df5.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df5.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df5 = df5[cols]
df5 = df5.to_numpy()

# convert into input/output
X5, y5 = split_sequences(df5, n_steps)
print(X5.shape, y5.shape)

(3812, 5, 12) (3812,)


/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [38]:
df6.drop("Date_Time", axis='columns', inplace=True)
df6.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df6.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df6 = df6[cols]
df6 = df6.to_numpy()

# convert into input/output
X6, y6 = split_sequences(df6, n_steps)
print(X6.shape, y6.shape)

(9662, 5, 12) (9662,)


/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [39]:
df7.drop("Date_Time", axis='columns', inplace=True)
df7.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df7.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df7 = df7[cols]
df7 = df7.to_numpy()

# convert into input/output
X7, y7 = split_sequences(df7, n_steps)
print(X7.shape, y7.shape)

/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



(4147, 5, 12) (4147,)


In [40]:
# Concatenating datasets
X_train = np.concatenate((X1,X2,X3,X4,X5,X6,X7))
y_train = np.concatenate((y1,y2,y3,y4,y5,y6,y7))

In [41]:
n_features = X_train.shape[2]

model = create_model()

# fit model
model.fit(X_train, y_train, epochs=1000, verbose=0)

In [42]:
# Save the weights
path = '/content/drive/MyDrive/Machine Learning Models/FYP/CNN1/'
model.save_weights(path)

# Import pre-trained weights

In [9]:
path = '/content/drive/MyDrive/Machine Learning Models/FYP/CNN1/'
# Create a new model instance
model = create_model()
# Restore the weights
model.load_weights(path)

# Testing on the same turbine

In [10]:
df8.drop("Date_Time", axis='columns', inplace=True)
df8.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df8.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df8 = df8[cols]
df8 = df8.to_numpy()

# convert into input/output
X8, y8 = split_sequences(df8, n_steps)
print(X8.shape, y8.shape)

(10689, 5, 12) (10689,)


/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [11]:
df9.drop("Date_Time", axis='columns', inplace=True)
df9.drop('Possible_Active_Power', axis='columns', inplace=True)
cols = df9.columns.tolist()
cols = cols[:5] + cols[6:] + [cols[5]]
df9 = df9[cols]
df9 = df9.to_numpy()

# convert into input/output
X9, y9 = split_sequences(df9, n_steps)
print(X9.shape, y9.shape)

(18559, 5, 12) (18559,)


/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [12]:
# Concatenating datasets
X_test = np.concatenate((X8,X9))
y_test = np.concatenate((y8,y9))

In [13]:
# demonstrate prediction
yhat = model.predict(X_test, verbose=0)

In [14]:
yhat = yhat.reshape(yhat.shape[0],)
df_final=pd.DataFrame({'y_hat':yhat,'y_test':y_test})

In [15]:
df_final['difference'] = df_final['y_hat']-df_final['y_test']
df_final["abs_difference"] = abs(df_final['y_hat']-df_final['y_test'])
print(df_final["difference"].mean())
print(df_final["abs_difference"].mean())

0.012706105859808376
0.03565381989292022


In [16]:
df_final.to_csv('drive/MyDrive/DatasetsWind/df_final.csv', index=False)

# Results, Plots

In [17]:
# Adding data_time column back
df8 = df['2018-06-01 00:00:00':'2018-08-14 06:50:00']
df9 = df['2018-08-21 07:00:00':]

frames = [df8, df9]
test = pd.concat(frames)
test.drop("Date_Time", axis='columns', inplace=True)
test = test.reset_index()
df_final["Date_Time"] = test["Date_Time"]

In [18]:
column_name = 'y_test' 
column_name1 = 'y_hat'

fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['Date_Time'], y=df_final[column_name], mode='lines', name='Actual'))
fig.add_trace(go.Scatter(x=df_final['Date_Time'],y=df_final[column_name1], mode='lines', name='Predicted'))
fig.update_layout(title_text= "Actual vs Predicted")

fig.show()

In [19]:
column_name = 'difference' 

fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['Date_Time'], y=df_final[column_name], mode='lines', name='Error'))
fig.update_layout(title_text= "Error")

fig.show()

In [20]:
column_name = 'abs_difference' 

fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['Date_Time'], y=df_final[column_name], mode='lines', name='Absolute Error'))
fig.update_layout(title_text= "Absolute Error")

fig.show()

Re-sampling data

In [21]:
#@title Resampling { display-mode: "form" }
sample_frequency = 60 #@param {type:"slider", min:20, max:120, step:10}
sample = str(sample_frequency) + "min"

In [22]:
df_final.set_index('Date_Time', inplace = True)
df_resample = df_final.resample(sample).mean().reset_index()
df_final = df_final.reset_index()

In [23]:
column_name = 'difference' 

fig = go.Figure()
fig.add_trace(go.Scatter(x=df_resample['Date_Time'], y=df_resample[column_name], mode='lines', name='Error'))
fig.update_layout(title_text= "Error")

fig.show()

In [24]:
column_name = 'abs_difference' 

fig = go.Figure()
fig.add_trace(go.Scatter(x=df_resample['Date_Time'], y=df_resample[column_name], mode='lines', name='Absolute Error'))
fig.update_layout(title_text= "Absolute Error")

fig.show()